In [18]:
import pandas as pd
import numpy as np
import os, sys, copy, argparse
import json
import sumolib, traci
from tqdm import tqdm
from datetime import datetime
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
path_scr = os.path.join(path_root, 'scripts')
sys.path.append(path_scr)
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [25]:
self = DailyPreprocessor(config_name='revised')

In [27]:
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()
self.make_match6()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-5. 테이블을 표준화했습니다.
1-6. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.


In [46]:
self.match6

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0         175         1         A        8        남        북       179   
1         175         1         B        4        북        남       003   
2         175         2         A        7        북        동       001   
3         175         2         B        3        남        서       179   
4         175         3         A        6        동        서       092   
..        ...       ...       ...      ...      ...      ...       ...   
103       210         2         B        2        서        동       270   
104       210         3         A        7        북        동       359   
105       210         3         B        4        북        남       000   
106       210         4         A        8        남        북       180   
107       210         4         B        3        남        서       180   

    out_angle    inc_edge_id   out_edge_id node_id node_type turn_type  
0         004  -571542797_02  571500487_01      i0    normal  straight  
1         176  -571500487_01  571542797_02      i0    normal  straight  
2         095  -571500487_01  571545870_01      i0    normal      left  
3         271  -571542797_02  571510153_01      i0    normal      left  
4         270   571545870_02  571510153_01      i0    normal  straight  
..        ...            ...           ...     ...       ...       ...  
103       090            NaN           NaN     u60    u_turn  straight  
104       090            NaN           NaN     u60    u_turn      left  
105       180            NaN           NaN     u60    u_turn  straight  
106       000            NaN           NaN     u60    u_turn  straight  
107       270            NaN           NaN     u60    u_turn      left  

[108 rows x 13 columns]

In [28]:
self.match7 = self.match6.copy()
self.match7 = self.match7[['inter_no', 'node_id', 'move_no', 'inc_angle', 'out_angle', 'inc_dire', 'out_dire', 'inc_edge_id', 'out_edge_id', 'node_type', 'turn_type']]

# (1) 각 교차로별 방향 목록 : pdires (possible directions)
p2dires = {} # parent_id to directions
for parent_id in self.parent_ids:
    dires = self.match7[self.match7.node_id == parent_id][['inc_dire','out_dire']].values.flatten()
    dires = {dire for dire in dires if type(dire)==str}
    p2dires[parent_id] = dires

# (2) 각 (교차로, 진입방향) 별 진입id 목록 : inc2id (incoming direction to incoming edge_id)
inc2id = {}
for parent_id in self.parent_ids:
    for inc_dire in p2dires[parent_id]:
        df = self.match7[(self.match7.node_id==parent_id) & (self.match7.inc_dire==inc_dire)]
        inc2id[(parent_id, inc_dire)] = df.inc_edge_id.iloc[0]

# (3) 각 (교차로, 진출방향) 별 진출id 목록 : out2id (outgoing direction to outgoing edge_id)
out2id = {}
for parent_id in self.parent_ids:
    for out_dire in p2dires[parent_id]:
        df = self.match7[(self.match7.node_id==parent_id) & (self.match7.out_dire==out_dire)]
        out2id[(parent_id, out_dire)] = df.out_edge_id.iloc[0]

# (4) 각 parent_id별 이동류번호 목록
p2move = dict() # parent id to a list of aligned movement numbers
for parent_id in self.parent_ids:
    pnema = self.nema[self.nema.inc_dire.isin(p2dires[parent_id]) & self.nema.out_dire.isin(p2dires[parent_id])]
    p2move[parent_id] = list(pnema.move_no)

# (5) 방위별 방향벡터
dire2vec = dict() # direction to unit vector
theta = np.pi/2
for dire in self.dires:
    dire2vec[dire] = np.array([np.cos(theta), np.sin(theta)])
    theta -= np.pi/4

# (6) 각 parent_id별 : 각 이동류별 진입/진출 엣지 id
p2move2inc_edge_id = dict() # parent id to move2inc_edge_id
p2move2out_edge_id = dict() # parent id to move2out_edge_id
for parent_id in self.parent_ids:
    move2inc_edge_id = dict() # plain movement to incoming edge id
    move2out_edge_id = dict() # plain movement to outgoing edge id
    for move_no in range(1,17):
        row = self.nema[self.nema.move_no==move_no].iloc[0]
        inc_dire = row.inc_dire
        out_dire = row.out_dire
        inc_vec_true = dire2vec[inc_dire]
        out_vec_true = dire2vec[out_dire]

        node = self.net.getNode(parent_id)
        # 교차로의 모든 (from / to) edges
        inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
        out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
        # 교차로의 모든 (from / to) unit vector
        inc_vecs = []
        for inc_edge in inc_edges:
            start = inc_edge.getShape()[-1]
            end = inc_edge.getShape()[-2]
            inc_vec = np.array(end) - np.array(start)
            inc_vec = inc_vec / (inc_vec ** 2).sum() ** 0.5
            inc_vecs.append(inc_vec)
        out_vecs = []
        for out_edge in out_edges:
            start = out_edge.getShape()[0]
            end = out_edge.getShape()[1]
            out_vec = np.array(end) - np.array(start)
            out_vec = out_vec / (out_vec ** 2).sum() ** 0.5
            out_vecs.append(out_vec)
        # 매칭 엣지 반환
        inc_index = np.array([np.dot(inc_vec, inc_vec_true) for inc_vec in inc_vecs]).argmax()
        out_index = np.array([np.dot(out_vec, out_vec_true) for out_vec in out_vecs]).argmax()
        inc_edge_id = inc_edges[inc_index].getID()
        out_edge_id = out_edges[out_index].getID()
        move2inc_edge_id[move_no] = inc_edge_id
        move2out_edge_id[move_no] = out_edge_id
    p2move2inc_edge_id[parent_id] = move2inc_edge_id
    p2move2out_edge_id[parent_id] = move2out_edge_id

# (7) 각 이동류별 진입/진출 방위
m2inc_dire = dict()
m2out_dire = dict()
for move_no in range(1,17):
    row = self.nema[self.nema.move_no==move_no].iloc[0]
    m2inc_dire[move_no] = row.inc_dire
    m2out_dire[move_no] = row.out_dire


In [45]:
p2move

{'i0': [1, 2, 3, 4, 5, 6, 7, 8],
 'i1': [3, 4, 5, 8],
 'i2': [4, 8],
 'i3': [1, 2, 3, 4, 5, 6, 7, 8],
 'i6': [1, 2, 3, 4, 5, 6, 7, 8],
 'i7': [4, 8],
 'i8': [1, 2, 3, 4, 5, 6, 7, 8],
 'i9': [2, 6]}

In [37]:
for parent_id in self.parent_ids:
    print(parent_id)
    for move_no in range(1,17):
        print(move_no)
        print(p2move2inc_edge_id[parent_id][move_no])
        print(p2move2inc_edge_id[parent_id][move_no])

i0
1
571545870_02
571545870_02
2
571510153_02
571510153_02
3
-571542797_02
-571542797_02
4
-571500487_01
-571500487_01
5
571510153_02
571510153_02
6
571545870_02
571545870_02
7
-571500487_01
-571500487_01
8
-571542797_02
-571542797_02
9
-571500487_01
-571500487_01
10
571510153_02
571510153_02
11
571545870_02
571545870_02
12
-571500487_01
-571500487_01
13
571510153_02
571510153_02
14
-571500487_01
-571500487_01
15
-571500487_01
-571500487_01
16
571545870_02
571545870_02
i1
1
571542797_02.99
571542797_02.99
2
571543469_02
571543469_02
3
-571542810_01
-571542810_01
4
571542797_02.99
571542797_02.99
5
571543469_02
571543469_02
6
571542797_02.99
571542797_02.99
7
571542797_02.99
571542797_02.99
8
-571542810_01
-571542810_01
9
571542797_02.99
571542797_02.99
10
-571542810_01
-571542810_01
11
-571542810_01
-571542810_01
12
571543469_02
571543469_02
13
-571542810_01
-571542810_01
14
571542797_02.99
571542797_02.99
15
571543469_02
571543469_02
16
-571542810_01
-571542810_01
i2
1
571542107_02
57

In [43]:
for parent_id in self.parent_ids:
    for move_no in range(1,17):
        row = self.nema[self.nema.move_no==move_no].iloc[0]
        inc_dire = row.inc_dire
        out_dire = row.out_dire
        inc_vec_true = dire2vec[inc_dire]
        out_vec_true = dire2vec[out_dire]

        node = self.net.getNode(parent_id)
        # 교차로의 모든 (from / to) edges
        inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
        out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
        # 교차로의 모든 (from / to) unit vector
        inc_vecs = []
        for inc_edge in inc_edges:
            start = inc_edge.getShape()[-1]
            end = inc_edge.getShape()[-2]
            inc_vec = np.array(end) - np.array(start)
            inc_vec = inc_vec / (inc_vec ** 2).sum() ** 0.5
            inc_vecs.append(inc_vec)
        out_vecs = []
        for out_edge in out_edges:
            start = out_edge.getShape()[0]
            end = out_edge.getShape()[1]
            out_vec = np.array(end) - np.array(start)
            out_vec = out_vec / (out_vec ** 2).sum() ** 0.5
            out_vecs.append(out_vec)
        # 매칭 엣지 반환
        inc_index = np.array([np.dot(inc_vec, inc_vec_true) for inc_vec in inc_vecs]).argmax()
        out_index = np.array([np.dot(out_vec, out_vec_true) for out_vec in out_vecs]).argmax()
        inc_edge_id = inc_edges[inc_index].getID()
        out_edge_id = out_edges[out_index].getID()
        print(row)
        print(inc_edge_id, out_edge_id)

move_no     1
inc_dire    동
out_dire    남
Name: 0, dtype: object
571545870_02 571542797_02
move_no     2
inc_dire    서
out_dire    동
Name: 1, dtype: object
571510153_02 571545870_01
move_no     3
inc_dire    남
out_dire    서
Name: 2, dtype: object
-571542797_02 571510153_01
move_no     4
inc_dire    북
out_dire    남
Name: 3, dtype: object
-571500487_01 571542797_02
move_no     5
inc_dire    서
out_dire    북
Name: 4, dtype: object
571510153_02 571500487_01
move_no     6
inc_dire    동
out_dire    서
Name: 5, dtype: object
571545870_02 571510153_01
move_no     7
inc_dire    북
out_dire    동
Name: 6, dtype: object
-571500487_01 571545870_01
move_no     8
inc_dire    남
out_dire    북
Name: 7, dtype: object
-571542797_02 571500487_01
move_no      9
inc_dire    북동
out_dire    남동
Name: 8, dtype: object
-571500487_01 571545870_01
move_no     10
inc_dire    남서
out_dire    북동
Name: 9, dtype: object
571510153_02 571500487_01
move_no     11
inc_dire    남동
out_dire    남서
Name: 10, dtype: object
571545870_

In [ ]:
# (8) 가능한 모든 이동류에 대하여 진입id, 진출id 배정 : matching
self.matching = []
for parent_id in self.parent_ids:
    inter_no = self.node2inter[parent_id]
    # 좌회전과 직진(1 ~ 16)
    for move_no in range(1,17):
        inc_dire = m2inc_dire[move_no]
        out_dire = m2out_dire[move_no]
        if move_no in p2move[parent_id]:
            inc_edge_id = inc2id[(parent_id, inc_dire)]
            out_edge_id = out2id[(parent_id, out_dire)]
        else:
            inc_edge_id = p2move2inc_edge_id[parent_id][move_no]
            out_edge_id = p2move2out_edge_id[parent_id][move_no]
        if (inc_edge_id, out_edge_id) in self.n2io2turn[parent_id]:
            turn_type = self.n2io2turn[parent_id][inc_edge_id, out_edge_id]
        else:
            turn_type = 'left' if move_no % 2 else 'straight'
        new_row = pd.DataFrame({'inter_no':[inter_no], 'node_id':[parent_id], 'move_no':[move_no],
                                'inc_dire':[inc_dire], 'out_dire':[out_dire],
                                'inc_edge_id':[inc_edge_id], 'out_edge_id':[out_edge_id],
                                'turn_type': turn_type})
        self.matching.append(new_row)


In [24]:
self.matching[self.matching.inter_no==175]

inter_no node_id  move_no    inc_edge_id   out_edge_id              state  \
0        175      i0        1   571545870_02  571542797_02  grrrgrrGgrrrrrgrr   
1        175      i0        2   571510153_02  571545870_01  grrrgrrrgrrrrrgGr   
2        175      i0        3  -571542797_02  571510153_01  grrrgrrrgrrrrGgrr   
3        175      i0        4  -571500487_01  571542797_02  gGGrgrrrgrrrrrgrr   
4        175      i0        5   571510153_02  571500487_01  grrrgrrrgrrrrrgrG   
5        175      i0        6   571545870_02  571510153_01  grrrgGGrgrrrrrgrr   
6        175      i0        7  -571500487_01  571545870_01  grrGgrrrgrrrrrgrr   
7        175      i0        8  -571542797_02  571500487_01  grrrgrrrgGGGGrgrr   
8        175      i0        9  -571500487_01  571545870_01  grrGgrrrgrrrrrgrr   
9        175      i0       10   571510153_02  571500487_01  grrrgrrrgrrrrrgrG   
10       175      i0       11   571545870_02  571510153_01  grrrgGGrgrrrrrgrr   
11       175      i0       12  -571500487_01  571545870_01  grrGgrrrgrrrrrgrr   
12       175      i0       13   571510153_02  571500487_01  grrrgrrrgrrrrrgrG   
13       175      i0       14  -571500487_01  571510153_01  Grrrgrrrgrrrrrgrr   
14       175      i0       15  -571500487_01  571500487_01  grrrgrrrgrrrrrgrr   
15       175      i0       16   571545870_02  571500487_01  grrrGrrrgrrrrrgrr   

   turn_type  
0       left  
1   straight  
2       left  
3   straight  
4       left  
5   straight  
6       left  
7   straight  
8       left  
9       left  
10  straight  
11      left  
12      left  
13  straight  
14      left  
15  straight

In [8]:
self = SignalGenerator()

In [9]:
self.prepare_data()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-5. 필요한 보조 객체들이 모두 준비되었습니다.


In [10]:
self.process_history()

2. 신호이력 테이블을 변환합니다.


In [17]:
fsec = self.present_time - 300
move = pd.read_csv(os.path.join(self.path_tables, 'move', f'move_{fsec}.csv'), index_col=0)
move

inter_no  phas_A  phas_B  move_A  move_B
0       175       2       2       7       3
0       176       1       1       8       4
0       177       1       1       8       4
0       178       1       1       8       4
0       201       1       1       8       3
0       202       1       1       6       2
0       206       1       1       8       4
0       210       1       1       6      18